In [1]:
import json
import numpy as np
from pathlib import Path
from sklearn.model_selection import train_test_split
from tensorflow.keras.preprocessing.text import Tokenizer
from tensorflow.keras.preprocessing.sequence import pad_sequences
from tensorflow.keras.utils import to_categorical

from tensorflow.keras.models import Model
from tensorflow.keras.layers import (
    Input,
    Embedding,
    LSTM,
    Concatenate,
    Dense,
    TimeDistributed,
)
from tensorflow.keras.callbacks import EarlyStopping
from sklearn.metrics import classification_report
from collections import Counter

2025-04-29 15:10:04.089483: I tensorflow/core/util/port.cc:153] oneDNN custom operations are on. You may see slightly different numerical results due to floating-point round-off errors from different computation orders. To turn them off, set the environment variable `TF_ENABLE_ONEDNN_OPTS=0`.
2025-04-29 15:10:04.096411: I external/local_xla/xla/tsl/cuda/cudart_stub.cc:32] Could not find cuda drivers on your machine, GPU will not be used.
2025-04-29 15:10:04.155120: I external/local_xla/xla/tsl/cuda/cudart_stub.cc:32] Could not find cuda drivers on your machine, GPU will not be used.
2025-04-29 15:10:04.201581: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:467] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
E0000 00:00:1745914204.252337  250474 cuda_dnn.cc:8579] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
E0000 00:00:1745914204.26

In [16]:
# Load raw data
with open("normalize_dataset.json", encoding="utf-8") as f:
    raw_data = json.load(f)

# Validasi lengkap
required_keys = {"tokens", "ner", "srl", "question", "answer", "type"}
valid_data = []
invalid_data = []

for idx, item in enumerate(raw_data):
    error_messages = []

    if not isinstance(item, dict):
        error_messages.append("bukan dictionary")

    missing_keys = required_keys - item.keys()
    if missing_keys:
        error_messages.append(f"missing keys: {missing_keys}")

    if not error_messages:
        # Cek tipe data dan None
        if (not isinstance(item["tokens"], list) or
            not isinstance(item["ner"], list) or
            not isinstance(item["srl"], list) or
            not isinstance(item["question"], list) or
            not isinstance(item["answer"], list) or
            not isinstance(item["type"], str)):
            error_messages.append("field type tidak sesuai")
    
    if error_messages:
        print(f"\n Index {idx} | Masalah: {', '.join(error_messages)}")
        print(json.dumps(item, indent=2, ensure_ascii=False))
        invalid_data.append(item)
        continue

    valid_data.append(item)

# Statistik
print(f"\n Jumlah data valid: {len(valid_data)} / {len(raw_data)}")
print(f" Jumlah data tidak valid: {len(invalid_data)}")

# Proses data valid
tokens = [[t.lower().strip() for t in item["tokens"]] for item in valid_data]
ner_tags = [item["ner"] for item in valid_data]
srl_tags = [item["srl"] for item in valid_data]
questions = [[token.lower().strip() for token in item["question"]] for item in valid_data]
answers = [[token.lower().strip() for token in item["answer"]] for item in valid_data]
types = [item["type"] for item in valid_data]

type_counts = Counter(types)

print(type_counts)



 Jumlah data valid: 261 / 261
 Jumlah data tidak valid: 0
Counter({'ftb': 180, 'tof': 45, 'none': 36})


In [3]:
# tokenize
token_tok = Tokenizer(lower=False, oov_token="UNK")
token_ner = Tokenizer(lower=False)
token_srl = Tokenizer(lower=False)
token_q = Tokenizer(lower=False)
token_a = Tokenizer(lower=False)
token_type = Tokenizer(lower=False)

token_tok.fit_on_texts(tokens)
token_ner.fit_on_texts(ner_tags)
token_srl.fit_on_texts(srl_tags)
token_q.fit_on_texts(questions)
token_a.fit_on_texts(answers)
token_type.fit_on_texts(types)


maxlen = 20

In [4]:

X_tok = pad_sequences(
    token_tok.texts_to_sequences(tokens), padding="post", maxlen=maxlen
)
X_ner = pad_sequences(
    token_ner.texts_to_sequences(ner_tags), padding="post", maxlen=maxlen
)
X_srl = pad_sequences(
    token_srl.texts_to_sequences(srl_tags), padding="post", maxlen=maxlen
)
y_q = pad_sequences(token_q.texts_to_sequences(questions), padding="post", maxlen=maxlen)
y_a = pad_sequences(token_a.texts_to_sequences(answers), padding="post", maxlen=maxlen)

print(set(types))

y_type = [seq[0] for seq in token_type.texts_to_sequences(types)]  # list of int
y_type = to_categorical(np.array(y_type) - 1, num_classes=len(token_type.word_index))



{'none', 'tof', 'ftb'}


In [5]:
X_tok_train, X_tok_test, X_ner_train, X_ner_test, X_srl_train, X_srl_test, \
y_q_train, y_q_test, y_a_train, y_a_test, y_type_train, y_type_test = train_test_split(
    X_tok, X_ner, X_srl, y_q, y_a, y_type, test_size=0.2, random_state=42
)

X_train = [X_tok_train, X_ner_train, X_srl_train]
X_test = [X_tok_test, X_ner_test, X_srl_test]

In [6]:

inp_tok = Input(shape=(None,), name="tok_input")
inp_ner = Input(shape=(None,), name="ner_input")
inp_srl = Input(shape=(None,), name="srl_input")

emb_tok = Embedding(input_dim=len(token_tok.word_index) + 1, output_dim=128)(inp_tok)
emb_ner = Embedding(input_dim=len(token_ner.word_index) + 1, output_dim=16)(inp_ner)
emb_srl = Embedding(input_dim=len(token_srl.word_index) + 1, output_dim=16)(inp_srl)

# emb_tok = Embedding(input_dim=..., output_dim=..., mask_zero=True)(inp_tok)
# emb_ner = Embedding(input_dim=..., output_dim=..., mask_zero=True)(inp_ner)
# emb_srl = Embedding(input_dim=..., output_dim=..., mask_zero=True)(inp_srl)

merged = Concatenate()([emb_tok, emb_ner, emb_srl])

x = LSTM(256, return_sequences=True)(merged)

out_question = TimeDistributed(Dense(len(token_q.word_index) + 1, activation="softmax"), name="question_output")(x)
out_answer = TimeDistributed(Dense(len(token_a.word_index) + 1, activation="softmax"), name="answer_output")(x)
out_type = Dense(len(token_type.word_index), activation="softmax", name="type_output")(
    x[:, 0, :]
)  # gunakan step pertama

model = Model(
    inputs=[inp_tok, inp_ner, inp_srl], outputs=[out_question, out_answer, out_type]
)
model.compile(
    optimizer="adam",
    loss={
        "question_output": "sparse_categorical_crossentropy",
        "answer_output": "sparse_categorical_crossentropy",
        "type_output": "categorical_crossentropy",
    },
    metrics={
        "question_output": "accuracy",
        "answer_output": "accuracy",
        "type_output": "accuracy",
    },
)

model.summary()

# ----------------------------------------------------------------------------
# 5. TRAINING
# ----------------------------------------------------------------------------
model.fit(
    X_train,
    {
        "question_output": np.expand_dims(y_q_train, -1),
        "answer_output": np.expand_dims(y_a_train, -1),
        "type_output": y_type_train,
    },
    batch_size=32,
    epochs=30,
    validation_split=0.1,
    callbacks=[EarlyStopping(patience=3, restore_best_weights=True)],
)

import pickle


model.save("new_model_lstm_qg.keras")
with open("tokenizers.pkl", "wb") as f:
    pickle.dump({
        "token": token_tok,
        "ner": token_ner,
        "srl": token_srl,
        "question": token_q,
        "answer": token_a,
        "type": token_type
    }, f)



2025-04-29 15:10:06.654453: E external/local_xla/xla/stream_executor/cuda/cuda_platform.cc:51] failed call to cuInit: INTERNAL: CUDA error: Failed call to cuInit: UNKNOWN ERROR (303)


Model: "functional"

┏━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━┓
┃ Layer (type)        ┃ Output Shape      ┃    Param # ┃ Connected to      ┃
┡━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━┩
│ tok_input           │ (None, None)      │          0 │ -                 │
│ (InputLayer)        │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ ner_input           │ (None, None)      │          0 │ -                 │
│ (InputLayer)        │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ srl_input           │ (None, None)      │          0 │ -                 │
│ (InputLayer)        │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ embedding           │ (None, None, 128) │     74,496 │ tok_input[0][0]   │
│ (Embedding)         │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ embedding_1         │ (None, None, 16)  │        352 │ ner_input[0][0]   │
│ (Embedding)         │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ embedding_2         │ (None, None, 16)  │        272 │ srl_input[0][0]   │
│ (Embedding)         │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ concatenate         │ (None, None, 160) │          0 │ embedding[0][0],  │
│ (Concatenate)       │                   │            │ embedding_1[0][0… │
│                     │                   │            │ embedding_2[0][0] │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ lstm (LSTM)         │ (None, None, 256) │    427,008 │ concatenate[0][0] │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ get_item (GetItem)  │ (None, 256)       │          0 │ lstm[0][0]        │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ question_output     │ (None, None, 339) │     87,123 │ lstm[0][0]        │
│ (TimeDistributed)   │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ answer_output       │ (None, None, 234) │     60,138 │ lstm[0][0]        │
│ (TimeDistributed)   │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ type_output (Dense) │ (None, 3)         │        771 │ get_item[0][0]    │
└─────────────────────┴───────────────────┴────────────┴───────────────────┘

 Total params: 650,160 (2.48 MB)

 Trainable params: 650,160 (2.48 MB)

 Non-trainable params: 0 (0.00 B)

Epoch 1/30
5/5 ━━━━━━━━━━━━━━━━━━━━ 3s 139ms/step - answer_output_accuracy: 0.4569 - answer_output_loss: 5.3719 - loss: 12.2246 - question_output_accuracy: 0.3854 - question_output_loss: 5.7392 - type_output_accuracy: 0.5172 - type_output_loss: 1.0955 - val_answer_output_accuracy: 0.9382 - val_answer_output_loss: 4.7459 - val_loss: 10.9338 - val_question_output_accuracy: 0.7618 - val_question_output_loss: 5.0968 - val_type_output_accuracy: 0.5294 - val_type_output_loss: 1.0911
Epoch 2/30
5/5 ━━━━━━━━━━━━━━━━━━━━ 0s 34ms/step - answer_output_accuracy: 0.9030 - answer_output_loss: 4.0847 - loss: 9.6638 - question_output_accuracy: 0.6989 - question_output_loss: 4.4100 - type_output_accuracy: 0.6659 - type_output_loss: 1.0841 - val_answer_output_accuracy: 0.9382 - val_answer_output_loss: 2.0126 - val_loss: 5.3872 - val_question_output_accuracy: 0.7618 - val_question_output_loss: 2.2876 - val_type_output_accuracy: 0.5294 - val_type_output_loss: 1.0870
Epoch 3/30
5/5 ━━━━━━━━━━━━━━━━━━━━ 0s 

In [10]:

def token_level_accuracy(y_true, y_pred):
    correct = 0
    total = 0
    for true_seq, pred_seq in zip(y_true, y_pred):
        for t, p in zip(true_seq, pred_seq):
            if t != 0:  # ignore padding
                total += 1
                if t == p:
                    correct += 1
    return correct / total if total > 0 else 0


# Predict on test set
y_pred_q, y_pred_a, y_pred_type = model.predict(X_test)

# Decode predictions to class indices
y_pred_q = np.argmax(y_pred_q, axis=-1)
y_pred_a = np.argmax(y_pred_a, axis=-1)
y_pred_type = np.argmax(y_pred_type, axis=-1)
y_true_type = np.argmax(y_type_test, axis=-1)

# Calculate token-level accuracy
acc_q = token_level_accuracy(y_q_test, y_pred_q)
acc_a = token_level_accuracy(y_a_test, y_pred_a)

# Type classification report
report_type = classification_report(y_true_type, y_pred_type, zero_division=0)

# Print Results
print("\n=== Akurasi Detail ===")
print(f"Question Accuracy (Token-level): {acc_q:.4f}")
print(f"Answer Accuracy (Token-level)  : {acc_a:.4f}")
print(f"Type Accuracy (Class-level)   : {np.mean(y_true_type == y_pred_type):.2f}")
# print("\n=== Classification Report (TYPE) ===")
# print(report_type)

2/2 ━━━━━━━━━━━━━━━━━━━━ 0s 18ms/step

=== Akurasi Detail ===
Question Accuracy (Token-level): 0.0000
Answer Accuracy (Token-level)  : 0.0000
Type Accuracy (Class-level)   : 0.61


In [8]:

# flat_true_a, flat_pred_a = flatten_valid(y_a_test, y_pred_a_class)
# print("\n=== Classification Report: ANSWER ===")
# print(classification_report(flat_true_a, flat_pred_a))


In [9]:

# print("\n=== Classification Report: TYPE ===")
# print(classification_report(y_true_type_class, y_pred_type_class))